In [2]:
import os
os.chdir('raw_dataset')

In [3]:
import json

In [4]:
from convokit import Corpus, Utterance, User

In [5]:
with open('friends_season_01.json', 'r') as f:
    s01_corpus_json = json.load(f)

In [6]:
s01_corpus_json['season_id']

's01'

In [7]:
s01_corpus_json

{'season_id': 's01',
 'episodes': [{'episode_id': 's01_e01',
   'scenes': [{'scene_id': 's01_e01_c01',
     'utterances': [{'utterance_id': 's01_e01_c01_u001',
       'speakers': ['Monica Geller'],
       'transcript': "There's nothing to tell! He's just some guy I work with!",
       'tokens': [['There', "'s", 'nothing', 'to', 'tell', '!'],
        ['He', "'s", 'just', 'some', 'guy', 'I', 'work', 'with', '!']],
       'transcript_with_note': None,
       'tokens_with_note': None,
       'character_entities': [[],
        [[0, 1, 'Paul the Wine Guy'],
         [4, 5, 'Paul the Wine Guy'],
         [5, 6, 'Monica Geller']]]},
      {'utterance_id': 's01_e01_c01_u002',
       'speakers': ['Joey Tribbiani'],
       'transcript': "C'mon, you're going out with the guy! There's gotta be something wrong with him!",
       'tokens': [["C'mon",
         ',',
         'you',
         "'re",
         'going',
         'out',
         'with',
         'the',
         'guy',
         '!'],
        

In [9]:
def convert_json_to_utterances(season_json):
    retval = []
    season_id = season_json['season_id']
    for episode in season_json['episodes']:
        episode_id = episode['episode_id']
        for scene in episode['scenes']:
            scene_id = scene['scene_id']
            reply_to = None
            for i, utt in enumerate(scene['utterances']):
                if i == 0:
                    reply_to = None
                    root = utt['utterance_id']
                else:
                    reply_to = utt_id # previous utt_id
                utt_id = utt['utterance_id']
                speakers = utt['speakers'][0] if len(utt['speakers']) > 0 else None
                transcript = utt['transcript']
                tokens = utt['tokens']
                transcript_note = utt['transcript_with_note']
                tokens_with_note = utt['tokens_with_note']
                character_entities = utt['character_entities']
                retval.append(Utterance(id=utt_id, 
                                        user=User(name=speakers),
                                        root=root,
                                        reply_to=reply_to,
                                        text=transcript,
                                        meta={
                                            'season': season_id,
                                            'episode': episode_id,
                                            'scene': scene_id,
                                            'tokens': tokens,
                                            'transcript_with_note': transcript_note,
                                            'tokens_with_note': tokens_with_note,
                                            'character_entities': character_entities
                                        }
                                       ))
    return retval

In [10]:
utts = convert_json_to_utterances(s01_corpus_json)

In [11]:
s01_corpus = Corpus(utterances=convert_json_to_utterances(s01_corpus_json))

In [12]:
s01_corpus.print_summary_stats()

Number of Users: 108
Number of Utterances: 6626
Number of Conversations: 326


In [13]:
list(s01_corpus.get_user('Ross Geller').iter_utterances())

[Utterance({'id': 's01_e01_c01_u021', 'user': User([('name', 'Ross Geller')]), 'root': 's01_e01_c01_u001', 'reply_to': 's01_e01_c01_u020', 'timestamp': None, 'text': 'Hi.', 'meta': {'season': 's01', 'episode': 's01_e01', 'scene': 's01_e01_c01', 'tokens': [['Hi', '.']], 'transcript_with_note': '(mortified) Hi.', 'tokens_with_note': [['(', 'mortified', ')', 'Hi', '.']], 'character_entities': [[]]}}),
 Utterance({'id': 's01_e01_c01_u024', 'user': User([('name', 'Ross Geller')]), 'root': 's01_e01_c01_u001', 'reply_to': 's01_e01_c01_u023', 'timestamp': None, 'text': 'I just feel like someone reached down my throat, grabbed my small intestine, pulled it out of my mouth and tied it around my neck...', 'meta': {'season': 's01', 'episode': 's01_e01', 'scene': 's01_e01_c01', 'tokens': [['I', 'just', 'feel', 'like', 'someone', 'reached', 'down', 'my', 'throat', ',', 'grabbed', 'my', 'small', 'intestine', ',', 'pulled', 'it', 'out', 'of', 'my', 'mouth', 'and', 'tied', 'it', 'around', 'my', 'neck',

In [14]:
s01_corpus.dump("corpus", base_path="../")